HELMET DETECTION USING YOLOV8M  - [ GITHUB : srdraghu]

In [1]:
import numpy as np
import pandas as pd

from pathlib import Path
import xml.etree.ElementTree as ET
from xml.dom.minidom import parse
from shutil import copyfile
import os

In [2]:
os.makedirs('Dataset/labels', exist_ok=True)
os.makedirs('Dataset/images', exist_ok=True)

classes = ['helmet', 'no helmet', 'person']

print("Directories created and classes defined.")

Directories created and classes defined.


In [3]:
classes = ['helmet','no helmet','person']

def convert_annot(size , box):
    x1 = int(box[0])
    y1 = int(box[1])
    x2 = int(box[2])
    y2 = int(box[3])

    dw = np.float32(1. / int(size[0]))
    dh = np.float32(1. / int(size[1]))

    w = x2 - x1
    h = y2 - y1
    x = x1 + (w / 2)
    y = y1 + (h / 2)

    x = x * dw
    w = w * dw
    y = y * dh
    h = h * dh
    return [x, y, w, h]

In [4]:
def save_txt_file(img_jpg_file_name, size, img_box):
    save_file_name = 'working/Dataset/labels/' +  img_jpg_file_name + '.txt'
    
    with open(save_file_name ,'a+') as file_path:
        for box in img_box:

            cls_num = classes.index(box[0])

            new_box = convert_annot(size, box[1:])

            file_path.write(f"{cls_num} {new_box[0]} {new_box[1]} {new_box[2]} {new_box[3]}\n")

        file_path.flush()
        file_path.close()

In [5]:
def get_xml_data(file_path, img_xml_file):
    img_path = file_path + '/' + img_xml_file + '.xml'

    tree = ET.parse(img_path)
    root = tree.getroot()

    img_name = root.find("filename").text
    img_size = root.find("size")
    img_w = int(img_size.find("width").text)
    img_h = int(img_size.find("height").text)
    img_c = int(img_size.find("depth").text)

    img_box = []
    for box in root.findall("object"):
        cls_name = box.find("name").text
        x1 = int(box.find("bndbox").find("xmin").text)
        y1 = int(box.find("bndbox").find("ymin").text)
        x2 = int(box.find("bndbox").find("xmax").text)
        y2 = int(box.find("bndbox").find("ymax").text)
        img_box.append([cls_name, x1, y1, x2, y2])

    img_jpg_file_name = img_xml_file + '.jpg'
    save_txt_file(img_xml_file, [img_w, img_h], img_box)

In [15]:
from tqdm import tqdm

files = os.listdir('input/hard-hat-detection/annotations')
for file in tqdm(files, total=len(files)):
    file_xml = file.split(".")
    get_xml_data('input/hard-hat-detection/annotations', file_xml[0])

100%|██████████| 5000/5000 [00:01<00:00, 3165.42it/s]


In [17]:
from sklearn.model_selection import train_test_split
image_list = os.listdir('input/hard-hat-detection/annotations')
train_list, test_list = train_test_split(image_list, test_size=0.2, random_state=42)
val_list, test_list = train_test_split(test_list, test_size=0.5, random_state=42)
print('total =', len(image_list))
print('train :', len(train_list))
print('val   :', len(val_list))
print('test  :', len(test_list))

total = 5000
train : 4000
val   : 500
test  : 500


In [23]:
from shutil import copyfile
import os

def copy_data(file_list, img_labels_root, imgs_source, mode):
    labels_path = os.path.join(img_labels_root, mode)
    images_path = os.path.join(imgs_source, mode)
    
    os.makedirs(labels_path, exist_ok=True)
    os.makedirs(images_path, exist_ok=True)

    for file in file_list:
        base_filename = os.path.splitext(os.path.basename(file))[0]
        
        img_src_file = os.path.join(imgs_source, base_filename + '.png')  # Assuming it's a .png image
        label_src_file = os.path.join(img_labels_root, base_filename + '.txt')
        
        img_dest_file = os.path.join(images_path, base_filename + '.png')
        label_dest_file = os.path.join(labels_path, base_filename + '.txt')

        # Check if image file exists before attempting to copy
        if os.path.exists(img_src_file):
            copyfile(img_src_file, img_dest_file)
        else:
            print(f"Image file {img_src_file} not found, skipping.")
        
        # Check if label file exists before attempting to copy
        if os.path.exists(label_src_file):
            copyfile(label_src_file, label_dest_file)
        else:
            print(f"Label file {label_src_file} not found, skipping.")

# Example usage
copy_data(train_list, 'working/Dataset/labels', 'working/Dataset/images', "train")
copy_data(val_list, 'working/Dataset/labels', 'working/Dataset/images', "val")
copy_data(test_list, 'working/Dataset/labels', 'working/Dataset/images', "test")


In [24]:
print('total =', len(image_list))
print('train :', len(train_list))
print('val   :', len(val_list))
print('test  :', len(test_list))

total = 5000
train : 4000
val   : 500
test  : 500


In [6]:
import yaml

config = {

   "train": "working/Dataset/images/train",
   "val": "working/Dataset/images/val",
   "test": "working/Dataset/images/test",
   "nc": 3,
   "names": ['helmet','no helmet','person']
}
with open("data.yaml", "w") as file:
   yaml.dump(config, file, default_flow_style=False)

In [8]:
with open('data.yaml', 'r') as file:
    content = file.read()
    print(content)


names:
- helmet
- no helmet
- person
nc: 3
test: C:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test
train: C:\Users\Student\Desktop\Helmet detection\working\Dataset\images\train
val: C:\Users\Student\Desktop\Helmet detection\working\Dataset\images\val



In [9]:
!yolo task=detect mode=train data=data.yaml model=yolov8m.pt epochs=100 lr0=0.01

Ultralytics YOLOv8.2.100 🚀 Python-3.11.8 torch-2.4.1+cu118 CUDA:0 (NVIDIA GeForce RTX 4080, 16376MiB)
engine\trainer: task=detect, mode=train, model=yolov8m.pt, data=data.yaml, epochs=100, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train3, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=True, show_


train: Scanning C:\Users\Student\Desktop\Helmet detection\working\Dataset\labels\train.cache... 4000 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4000/4000 [00:00<?, ?it/s]
train: Scanning C:\Users\Student\Desktop\Helmet detection\working\Dataset\labels\train.cache... 4000 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4000/4000 [00:00<?, ?it/s]

val: Scanning C:\Users\Student\Desktop\Helmet detection\working\Dataset\labels\val.cache... 500 images, 0 backgrounds, 0 corrupt: 100%|██████████| 500/500 [00:00<?, ?it/s]
val: Scanning C:\Users\Student\Desktop\Helmet detection\working\Dataset\labels\val.cache... 500 images, 0 backgrounds, 0 corrupt: 100%|██████████| 500/500 [00:00<?, ?it/s]

  0%|          | 0/250 [00:00<?, ?it/s]
      1/100      6.73G      2.291      6.024      1.846         81        640:   0%|          | 0/250 [00:00<?, ?it/s]
      1/100      6.73G      2.291      6.024      1.846         81        640:   0%|          | 1/250 [00:00<03:28,  1.19it/s]
      1/1

In [10]:
!yolo task=detect mode=val model=runs/detect/train3/weights/best.pt data=data.yaml save_json = True

Ultralytics YOLOv8.2.100 🚀 Python-3.11.8 torch-2.4.1+cu118 CUDA:0 (NVIDIA GeForce RTX 4080, 16376MiB)
Model summary (fused): 218 layers, 25,841,497 parameters, 0 gradients, 78.7 GFLOPs
                   all        500       2582      0.626      0.612      0.636      0.427
                helmet        452       1846      0.945      0.923      0.967      0.654
             no helmet         94        614      0.839      0.896       0.92      0.618
                person         19        122     0.0938     0.0164      0.021    0.00964
Speed: 0.4ms preprocess, 5.0ms inference, 0.0ms loss, 0.5ms postprocess per image
Saving runs\detect\val2\predictions.json...
Results saved to runs\detect\val2
💡 Learn more at https://docs.ultralytics.com/modes/val



val: Scanning C:\Users\Student\Desktop\Helmet detection\working\Dataset\labels\val.cache... 500 images, 0 backgrounds, 0 corrupt: 100%|██████████| 500/500 [00:00<?, ?it/s]
val: Scanning C:\Users\Student\Desktop\Helmet detection\working\Dataset\labels\val.cache... 500 images, 0 backgrounds, 0 corrupt: 100%|██████████| 500/500 [00:00<?, ?it/s]

                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   0%|          | 0/32 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   3%|▎         | 1/32 [00:00<00:12,  2.48it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   6%|▋         | 2/32 [00:00<00:08,  3.73it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):   9%|▉         | 3/32 [00:00<00:06,  4.64it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95):  12%|█▎        | 4/32 [0

In [11]:
!yolo task=detect mode=predict model=runs/detect/train3/weights/best.pt conf=0.25 source="working/Dataset/images/test" save_txt=True save=True

Ultralytics YOLOv8.2.100 🚀 Python-3.11.8 torch-2.4.1+cu118 CUDA:0 (NVIDIA GeForce RTX 4080, 16376MiB)
Model summary (fused): 218 layers, 25,841,497 parameters, 0 gradients, 78.7 GFLOPs

image 1/500 c:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test\hard_hat_workers1004.png: 640x640 7 helmets, 0.0ms
image 2/500 c:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test\hard_hat_workers1012.png: 640x640 5 helmets, 4.8ms
image 3/500 c:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test\hard_hat_workers1023.png: 640x640 8 helmets, 0.0ms
image 4/500 c:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test\hard_hat_workers1036.png: 640x640 3 helmets, 0.0ms
image 5/500 c:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test\hard_hat_workers1038.png: 640x640 1 helmet, 14 no helmets, 5.6ms
image 6/500 c:\Users\Student\Desktop\Helmet detection\working\Dataset\images\test\hard_hat_workers1052.png: 640x640 4 helmets, 9.5ms
im

In [12]:
!yolo task=detect mode=predict model=runs/detect/train3/weights/best.pt source='test.mp4'

Ultralytics YOLOv8.2.100 🚀 Python-3.11.8 torch-2.4.1+cu118 CUDA:0 (NVIDIA GeForce RTX 4080, 16376MiB)
Model summary (fused): 218 layers, 25,841,497 parameters, 0 gradients, 78.7 GFLOPs

video 1/1 (frame 1/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 30.8ms
video 1/1 (frame 2/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 0.0ms
video 1/1 (frame 3/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 0.0ms
video 1/1 (frame 4/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 4.1ms
video 1/1 (frame 5/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 0.0ms
video 1/1 (frame 6/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 12.9ms
video 1/1 (frame 7/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no helmet, 7.6ms
video 1/1 (frame 8/895) c:\Users\Student\Desktop\Helmet detection\test.mp4: 384x640 1 no he